In [1]:
import numpy as np
import pandas as pd
import sys
import os
from codebase.file_utils import save_obj, load_obj
from codebase.post_process import samples_to_df, get_topn_eig
import altair as alt
alt.data_transformers.disable_max_rows()

%load_ext autoreload
%autoreload 2

In [46]:
ppp = False
log_dir = "./log/cont_dat_simulation/CV/sim0/run3/20200526_085211___s0m0//"
data = load_obj('data', log_dir)

if ppp: 
    ps = load_obj('ps', log_dir)
    ps.keys()
else: 
    print("\n\nChecking data integrity...\n\n")
    complete_data = load_obj("complete_data", log_dir)

    ps = dict()
    ps[0] = load_obj('ps_0', log_dir)
    ps[1] = load_obj('ps_1', log_dir)
    ps[2] = load_obj('ps_2', log_dir)





Checking data integrity...




In [47]:
data

{'random_seed': 0,
 'N': 1000,
 'K': 2,
 'J': 6,
 'alpha': array([0., 0., 0., 0., 0., 0.]),
 'beta': array([[1. , 0. ],
        [0.8, 0. ],
        [0.8, 0. ],
        [0. , 1. ],
        [0. , 0.8],
        [0. , 0.8]]),
 'sigma_z': array([0.80622577, 0.80622577]),
 'Phi_corr': array([[1. , 0.2],
        [0.2, 1. ]]),
 'Phi_cov': array([[0.65, 0.13],
        [0.13, 0.65]]),
 'Marg_cov': array([[1.    , 0.52  , 0.52  , 0.13  , 0.104 , 0.104 ],
        [0.52  , 1.    , 0.416 , 0.104 , 0.0832, 0.0832],
        [0.52  , 0.416 , 1.    , 0.104 , 0.0832, 0.0832],
        [0.13  , 0.104 , 0.104 , 1.    , 0.52  , 0.52  ],
        [0.104 , 0.0832, 0.0832, 0.52  , 1.    , 0.416 ],
        [0.104 , 0.0832, 0.0832, 0.52  , 0.416 , 1.    ]]),
 'Theta': array([[0.35 , 0.   , 0.   , 0.   , 0.   , 0.   ],
        [0.   , 0.584, 0.   , 0.   , 0.   , 0.   ],
        [0.   , 0.   , 0.584, 0.   , 0.   , 0.   ],
        [0.   , 0.   , 0.   , 0.35 , 0.   , 0.   ],
        [0.   , 0.   , 0.   , 0.   , 0.584,

In [48]:
print(open(log_dir+'model.txt').read())

data {
  int<lower=1> N;
  int<lower=1> K;
  int<lower=1> J;
  matrix[N,J] yy;
}

transformed data{
  cov_matrix[J] I = diag_matrix(rep_vector(1, J));
}

parameters {
  cov_matrix[J] Marg_cov;
  vector[J] alpha;
}

model {
  to_vector(alpha) ~ normal(0, 10);
  Marg_cov ~ inv_wishart(J+2, I);
  for (n in 1:N){
    yy[n, ] ~ multi_normal(alpha,  Marg_cov);
  }
}



In [49]:
if ppp:
    num_chains = ps['alpha'].shape[1]
    num_samples = ps['alpha'].shape[0]
    num_of_factors = ps['beta'].shape[3]
    ps['beta_rot'] = ps['beta'].copy()

    for chain_number in range(ps['alpha'].shape[1]):
        for i in range(num_samples):
            if True: #num_of_factors==1:
                sign1 = np.sign(ps['beta'][i,chain_number,0,0])
                ps['beta_rot'][i,chain_number,:,0] = ps['beta'][i,chain_number,:,0] * sign1
                sign2 = np.sign(ps['beta'][i,chain_number,1,1])
                ps['beta_rot'][i,chain_number,1:,1] = ps['beta'][i,chain_number,1:,1] * sign2
#             else:
#                 b = ps['beta'][i,chain_number]
#                 ps['beta_rot'][i,chain_number] = get_topn_eig(b@b.T, num_of_factors)['P']

else: 
    num_chains = ps[0]['alpha'].shape[1]
    num_samples = ps[0]['alpha'].shape[0]
    num_of_factors = ps[0]['beta'].shape[3]
    for j in range(3):
        beta_rot = np.empty_like(ps[j]['beta'])
        for chain_number in range(num_chains):
            for i in range(num_samples):
                b = ps[j]['beta'][i,chain_number]
                beta_rot[i,chain_number] = get_topn_eig(b@b.T, num_of_factors)['P']
        ps[j]['beta_rot']= beta_rot

KeyError: 'beta'

In [50]:
samples_to_df(ps[0], 'beta_rot').head()

KeyError: 'beta_rot'

In [52]:
plotdata = samples_to_df(ps[0], 'alpha')
c1 = alt.Chart(plotdata).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'col:O'
).properties(width = 200, height=100, title='Beta') 

c1.interactive()

alt.Chart(...)

In [45]:
plotdata = samples_to_df(ps[0], 'beta_rot')
c1 = alt.Chart(plotdata).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'col:O'
).properties(width = 200, height=100, title='Beta') 

c1.interactive()

alt.Chart(...)

In [16]:
np.round(np.mean(np.mean(ps['beta_rot'],0),0),2)

KeyError: 'beta_rot'

In [107]:
np.round(np.mean(np.mean(ps['beta'],0),0),2)

array([[ 1.32,  0.  ],
       [ 1.39,  1.1 ],
       [ 2.25, -0.17],
       [ 0.57,  0.97],
       [ 0.57,  1.1 ],
       [ 0.93,  1.51]])

In [ ]:
c1 = alt.Chart(samples_to_df(ps, 'alpha')).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'cn:N'
).properties(width = 200, height=100) 

c1.interactive()